In [1]:
import os
import requests
import time
import boto3
import pandas as pd
import jupyter_black
from io import BytesIO
from io import StringIO
from tqdm.notebook import tqdm
import altair as alt
import matplotlib.pyplot as plt

In [2]:
jupyter_black.load()
pd.options.display.max_columns = 2000
pd.options.display.max_rows = 1000
pd.options.display.max_colwidth = None
alt.data_transformers.disable_max_rows()

DataTransformerRegistry.enable('default')

In [3]:
# Headers for requests
headers = {
    "sec-ch-ua": '"Chromium";v="124", "Google Chrome";v="124", "Not-A.Brand";v="99"',
    "User-Agent": "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/124.0.0.0 Safari/537.36",
    "sec-ch-ua-platform": '"macOS"',
}

In [4]:
# Shohei Ohtani
player = "660271"

In [5]:
batter_list = requests.get(
    "https://bdfed.stitch.mlbinfra.com/bdfed/stats/player?&env=prod&season=2024&sportId=1&stats=season&group=hitting&gameType=R&offset=0&sortStat=homeRuns&order=desc&teamId=119",
    headers=headers,
)

In [26]:
batters = pd.DataFrame(batter_list.json()["stats"])

In [27]:
batters.query('playerName == "Shohei Ohtani"').iloc[0]

year                                           2024
playerId                                     660271
playerName                            Shohei Ohtani
type                                         player
rank                                              1
playerFullName                        Shohei Ohtani
playerFirstName                              Shohei
playerLastName                               Ohtani
playerUseName                                Shohei
playerInitLastName                         S Ohtani
teamId                                          119
teamAbbrev                                      LAD
teamName                        Los Angeles Dodgers
teamShortName                               Dodgers
leagueName                                       NL
leagueId                                        104
positionAbbrev                                   DH
position                          Designated Hitter
primaryPositionAbbrev                           TWP
plateAppeara

In [31]:
players_ids = batters.query('playerName == "Shohei Ohtani"')["playerId"].to_list()

In [32]:
players_ids

[660271]

In [33]:
last_pitch_list = []

for player in tqdm(players_ids):

    headers = {
        "accept": "*/*",
        "user-agent": "Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/124.0.0.0 Safari/537.36",
        "x-requested-with": "XMLHttpRequest",
    }

    params = {
        "playerId": player,
        "type": "",
        "season": "2024",
    }

    pitch_data = requests.get(
        "https://baseballsavant.mlb.com/player-viz/lookup",
        params=params,
        headers=headers,
    ).json()["data"]

    last_pitch_src = pd.DataFrame(pitch_data).query("is_lastpitch == 1").fillna("")
    last_pitch_list.append(last_pitch_src)
    # time.sleep(3)

  0%|          | 0/1 [00:00<?, ?it/s]

In [34]:
pitch_df = pd.concat(last_pitch_list)

In [35]:
pitch_df["game_date"] = pd.to_datetime(pitch_df["game_date"])
pitch_df = pitch_df.sort_values("game_date").copy()

In [36]:
pitch_df["pa_number"] = pitch_df.groupby(["batter_name"])["play_id"].cumcount()

In [37]:
pitch_df["batter_name_clean"] = (
    pitch_df["batter_name"].str.split(", ", expand=True)[1]
    + " "
    + pitch_df["batter_name"].str.split(", ", expand=True)[0]
)

In [38]:
positive = [
    "Hit by pitch",
    "Field error",
    # "Strikeout",
    # "Field out",
    "Single",
    "Walk",
    "Fielders choice",
    "Sac fly",
    # "Double play",
    # "Force out",
    "Double",
    "Home run",
    # "Grounded into double play",
    "Triple",
    # "Caught stealing second",
    # "Catcher interf",
    "Sac bunt",
    # "Pickoff caught stealing third",
]

pitch_df["positive_outcome"] = pitch_df["events"].isin(positive)

In [39]:
slim_cols = [
    "player_id",
    "batter_name_clean",
    "pa_number",
    "events",
    "event_type",
    "inning",
    "des",
    "game_date",
    "game_year",
    "is_hit_into_play",
    "is_hit_into_play_basehit",
    "positive_outcome",
]

In [40]:
pitch_df["game_date"] = pitch_df["game_date"].astype(str)
pitch_df["player_id"] = pitch_df["player_id"].astype(str)
pitch_df["game_year"] = pitch_df["game_year"].astype(str)
pitch_df["des"] = pitch_df["des"].str.replace(".   ", ". ").str.replace(".  ", ". ")

In [41]:
pitch_df["events"] = (
    pitch_df["events"]
    .str.strip()
    .str.replace("_", " ")
    .str.replace("2b", "second")
    .str.replace("3b", "third")
    .str.capitalize()
)

In [42]:
pitch_df["event_type"] = (
    pitch_df["event_type"].str.strip().str.replace("_", " ").str.capitalize()
)

In [43]:
df = pitch_df.query("game_date > '2024-03-27'").copy()

In [44]:
df.sort_values("game_date", inplace=True)
df["cumulative_hrs"] = df["events"].eq("Home run").cumsum()

In [45]:
# Latest cumulative home runs
current_home_runs = df["cumulative_hrs"].iloc[-1]

# Total games played so far, assuming one entry per game (if that's not the case, adjust accordingly)
current_games_played = df["game_date"].nunique()

In [46]:
len(df.game_date.unique())

148

In [47]:
df

player_id     batter_name            pitcher_name  batter  pitcher  \
2643    660271  Ohtani, Shohei          O'Brien, Riley  660271   676617   
2642    660271  Ohtani, Shohei          Mikolas, Miles  660271   571945   
2637    660271  Ohtani, Shohei          Mikolas, Miles  660271   571945   
2633    660271  Ohtani, Shohei          Mikolas, Miles  660271   571945   
2628    660271  Ohtani, Shohei          Thompson, Zack  660271   668868   
2622    660271  Ohtani, Shohei      Gallegos, Giovanny  660271   606149   
2620    660271  Ohtani, Shohei          Thompson, Zack  660271   668868   
2616    660271  Ohtani, Shohei          Thompson, Zack  660271   668868   
2606    660271  Ohtani, Shohei            Romero, JoJo  660271   668941   
2593    660271  Ohtani, Shohei      Gallegos, Giovanny  660271   606149   
2604    660271  Ohtani, Shohei           Helsley, Ryan  660271   664854   
2587    660271  Ohtani, Shohei             Lynn, Lance  660271   458681   
2597    660271  Ohtani, Shohei     Liberatore, Matthew  660271   669461   
2605    660271  Ohtani, Shohei             Lynn, Lance  660271   458681   
2569    660271  Ohtani, Shohei            Matz, Steven  660271   571927   
2578    660271  Ohtani, Shohei            Matz, Steven  660271   571927   
2576    660271  Ohtani, Shohei         Pallante, Andre  660271   669467   
2571    660271  Ohtani, Shohei            Matz, Steven  660271   571927   
2559    660271  Ohtani, Shohei             Avila, Nick  660271   687014   
2563    660271  Ohtani, Shohei            Winn, Keaton  660271   676775   
2556    660271  Ohtani, Shohei            Winn, Keaton  660271   676775   
2547    660271  Ohtani, Shohei            Winn, Keaton  660271   676775   
2540    660271  Ohtani, Shohei             Webb, Logan  660271   657277   
2538    660271  Ohtani, Shohei             Webb, Logan  660271   657277   
2534    660271  Ohtani, Shohei             Webb, Logan  660271   657277   
2546    660271  Ohtani, Shohei          Rogers, Taylor  660271   573124   
2516    660271  Ohtani, Shohei          Harrison, Kyle  660271   690986   
2529    660271  Ohtani, Shohei          Harrison, Kyle  660271   690986   
2524    660271  Ohtani, Shohei          Rogers, Taylor  660271   573124   
2522    660271  Ohtani, Shohei          Harrison, Kyle  660271   690986   
2504    660271  Ohtani, Shohei             Smyly, Drew  660271   592767   
2513    660271  Ohtani, Shohei         Hendricks, Kyle  660271   543294   
2499    660271  Ohtani, Shohei         Hendricks, Kyle  660271   543294   
2500    660271  Ohtani, Shohei         Hendricks, Kyle  660271   543294   
2507    660271  Ohtani, Shohei    Merryweather, Julian  660271   657240   
2479    660271  Ohtani, Shohei           Wicks, Jordan  660271   696136   
2494    660271  Ohtani, Shohei            Little, Luke  660271   681432   
2488    660271  Ohtani, Shohei           Wicks, Jordan  660271   696136   
2486    660271  Ohtani, Shohei        Leiter Jr., Mark  660271   643410   
2477    660271  Ohtani, Shohei           Wicks, Jordan  660271   696136   
2463    660271  Ohtani, Shohei        Palencia, Daniel  660271   694037   
2469    660271  Ohtani, Shohei        Leiter Jr., Mark  660271   643410   
2467    660271  Ohtani, Shohei          Imanaga, Shota  660271   684007   
2461    660271  Ohtani, Shohei          Imanaga, Shota  660271   684007   
2460    660271  Ohtani, Shohei           Okert, Steven  660271   595345   
2453    660271  Ohtani, Shohei            Ober, Bailey  660271   641927   
2450    660271  Ohtani, Shohei        Funderburk, Kody  660271   681892   
2446    660271  Ohtani, Shohei            Jackson, Jay  660271   543351   
2441    660271  Ohtani, Shohei            Ober, Bailey  660271   641927   
2432    660271  Ohtani, Shohei          Stewart, Brock  660271   592779   
2437    660271  Ohtani, Shohei          Varland, Louie  660271   686973   
2434    660271  Ohtani, Shohei             Sands, Cole  660271   663485   
2429    660271  Ohtani, Shohei